![IBGE LOGO](https://www.infoescola.com/wp-content/uploads/2008/02/IBGE.png)



## API IBGE Noticias


In [0]:
from delta.tables import *
from pyspark.sql.types import *
from pyspark.sql.functions import col
import datetime, pytz
from pyspark.sql.functions import lit
from pyspark.sql import Window
from pyspark.sql.functions import *

import requests
import json

In [0]:
class RawLayerIngestion:
  
  def __init__(self,url,first_page,raw_directory):
    self.URL_API = url
    self.first_page = first_page
    self.raw_directory = raw_directory

  def raw_ingestion(self):

    try:
      valor_maximo_raw = [int(i.name.split('_')[1].replace("/","")) for i in dbutils.fs.ls(self.raw_directory)]
      valor_maximo_raw.sort()
      valor_maximo_raw = valor_maximo_raw[-1]
      ## Verificando numero total de paginas ##
      content_json = requests.get("{url}?page={page}".format(url=self.URL_API,page=self.first_page))
      content_json = content_json.json()
      print("Ultima pagina inserida na RAw ==>  " ,valor_maximo_raw)
      acumulo_paginas = []
      contador = valor_maximo_raw
      if valor_maximo_raw < content_json["totalPages"]:

        print(f"Iniciando Proceeso a partit da pagina ==> {contador}")
        while contador <= content_json["totalPages"]:
          noticias_API = requests.get("{url}?page={contador}".format(url=self.URL_API,contador=contador))
          noticias_json = noticias_API.json()
          acumulo_paginas.append(noticias_json["items"])

          if noticias_json["items"] != [] and str(noticias_json["page"])[-1] == "0":

            result_acumulo_paginas =[acumulo_paginas[i][item] for i in range(0,len(acumulo_paginas))
                                                                for item in range(0,len(acumulo_paginas[i]))]   
            df = spark.createDataFrame(result_acumulo_paginas).withColumn(f'to_the_page',lit(contador))
            print(f"\t Gravando até a pagina {contador}  no diretorio dbfs {self.raw_directory}")
            df.write.mode("overwrite").json(f'{self.raw_directory}filetothepage_{contador}')
            acumulo_paginas = []
          elif  noticias_json["page"] == content_json["totalPages"]:
            ### Ajuntando todas as paginas appendadas em uma lista unica ####
            result_acumulo_paginas =[acumulo_paginas[i][item] for i in range(0,len(acumulo_paginas))
                                                                    for item in range(0,len(acumulo_paginas[i]))]  
            df = spark.createDataFrame(result_acumulo_paginas).withColumn(f'to_the_page',lit(contador))
            print(f"\t Gravando a pagina {contador}  no diretorio dbfs {self.raw_directory}")
            df.write.mode("overwrite").json(f'{self.raw_directory}filetothepage_{contador}')
            acumulo_paginas = []

          contador = contador +1
        print("Processo finalizado")
      else:
        print("Todas as paginas da API ja foram inseridas na camada RAW")

    except:
      try:
        print("Nao possui arquivos")
        print("Buscando noticias desde a pagina 1....")
        noticias_API = requests.get("{url}?page={page}".format(url=self.URL_API,page=self.first_page))
        noticias_json = noticias_API.json()
        acumulo_paginas = []
        contador = 1
        while contador <= noticias_json["totalPages"]:
          noticias_API = requests.get("{url}?page={contador}".format(url=self.URL_API,contador=contador))
          noticias_json = noticias_API.json()
          acumulo_paginas.append(noticias_json["items"])

          if noticias_json["items"] != [] and str(noticias_json["page"])[-1] == "0":

            result_acumulo_paginas =[acumulo_paginas[i][item] for i in range(0,len(acumulo_paginas))
                                                                for item in range(0,len(acumulo_paginas[i]))]   
            
            df = spark.createDataFrame(result_acumulo_paginas).withColumn(f'to_the_page',lit(contador))
            print(f"\t Gravando até a pagina {contador}  no diretorio dbfs {self.raw_directory}")
            df.write.mode("overwrite").json(f'{self.raw_directory}filetothepage_{contador}')
            acumulo_paginas = []
          elif noticias_json["page"] == noticias_json["totalPages"]:
            print(f"Gravando todas as paginas até {contador}  no diretorio dbfs {self.raw_directory}")
            ### Ajuntando todas as paginas appendadas em uma lista unica ####
            result_acumulo_paginas =[acumulo_paginas[i][item] for i in range(0,len(acumulo_paginas))
                                                                  for item in range(0,len(acumulo_paginas[i]))]  
            
            df = spark.createDataFrame(result_acumulo_paginas).withColumn(f'to_the_page',lit(contador))
            df.write.mode("overwrite").json(f'{self.raw_directory}filetothepage_{contador}')
            acumulo_paginas = []
          contador = contador +1
        print("Processo finalizado")
      except Exception as e:
        print(f"===>>>> {e}")

  def start_run(self):
    self.raw_ingestion()
  



In [0]:
ingestao_raw = RawLayerIngestion('http://servicodados.ibge.gov.br/api/v3/noticias/',1,'dbfs:/mnt/raw_3/')
ingestao_raw.start_run()

Ultima pagina inserida na RAw ==>   203
Todas as paginas da API ja foram inseridas na camada RAW


In [0]:
df2 = spark.read.json('dbfs:/mnt/raw_3/*')

df2.display()


data_publicacao destaque editorias id imagens introducao link produto_id produtos produtos_relacionados tipo titulo to_the_page 20/06/2018 10:00:00 true geociencias 21494 {"image_intro":"","float_intro":"","image_intro_alt":"#PraCegoVer Vista a\u00e9rea de S\u00e3o Paulo","image_intro_caption":"","image_fulltext":"images\/agenciadenoticias\/geociencias\/2017-07\/areas_urbanizadas_release.jpg","float_fulltext":"","image_fulltext_alt":"#PraCegoVer Vista a\u00e9rea de S\u00e3o Paulo","image_fulltext_caption":""} O IBGE lança hoje a segunda parte da publicação Áreas Urbanizadas do Brasil 2015, que engloba as concentrações urbanas com população entre 100 mil e 300 mil habitantes. Nessa etapa, foram adotados os mesmos procedimentos metodológicos da primeira fase,... http://agenciadenoticias.ibge.gov.br/agencia-sala-de-imprensa/2013-agencia-de-noticias/releases/21494-ibge-apresenta-panorama-da-urbanizacao-no-brasil.html 15789 15789|Áreas Urbanizadas|areas-urbanizadas|2266 15789 Release IBGE apresenta panorama da urbanização no Brasil 100 18/06/2018 10:00:35 true economicas 21483 {"image_intro":"images\/agenciadenoticias\/estatisticas_economicas\/2018_06\/milho_thumb.jpg","float_intro":"","image_intro_alt":"#praCegoVer Milhos prontos para comer colocados sobre uma mesa","image_intro_caption":"","image_fulltext":"images\/agenciadenoticias\/estatisticas_economicas\/2018_06\/milho_home.jpg","float_fulltext":"","image_fulltext_alt":"#praCegoVer Milhos prontos para comer colocados sobre uma mesa","image_fulltext_caption":""} Estimativas da produção de milho são de 84,5 milhões t em 2018 Canjica, cuscuz, mungunzá, pamonha, pipoca, bolo de fubá são alguns exemplos de pratos típicos muito consumidos nas festas juninas em todo o país. Seu ingrediente indispensável é o milho, que... http://agenciadenoticias.ibge.gov.br/agencia-noticias/2012-agencia-de-noticias/noticias/21483-popular-nas-festas-juninas-milho-tem-alta-producao-no-pais.html 0 Notícia Popular nas festas juninas, milho tem alta produção no país 100 15/06/2018 09:00:00 true ibge 21468 {"image_intro":"images\/agenciadenoticias\/ibge\/2018_06\/copajogadores_thumb.jpg","float_intro":"","image_intro_alt":"#PraCegoVer jogadores da sele\u00e7\u00e3o se abra\u00e7am, comemorando gol","image_intro_caption":"","image_fulltext":"images\/agenciadenoticias\/ibge\/2018_06\/copajogadores_home.jpg","float_fulltext":"","image_fulltext_alt":"#PraCegoVer jogadores da sele\u00e7\u00e3o se abra\u00e7am, comemorando gol","image_fulltext_caption":""} Além de pesquisas e indicadores como os divulgados pelo IBGE, a estatística tem como outra utilidade o cálculo de probabilidades, como as de chances de título das seleções na Copa do Mundo. Esse é o foco do trabalho desenvolvido por Marcelo Leme de... http://agenciadenoticias.ibge.gov.br/agencia-noticias/2012-agencia-de-noticias/noticias/21468-quem-vai-vencer-projecoes-no-futebol-divulgam-estatistica.html 0 Notícia Quem vai vencer? Projeções no futebol divulgam estatística 100 14/06/2018 09:00:00 true economicas 21438 {"image_intro":"","float_intro":"","image_intro_alt":"","image_intro_caption":"","image_fulltext":"images\/agenciadenoticias\/releases_2017\/PMS_release.jpg","float_fulltext":"","image_fulltext_alt":"","image_fulltext_caption":""} Em abril, pela primeira vez no ano, o setor de serviços cresceu frente ao mês anterior, avançando 1,0% em relação a março (série com ajuste sazonal). Em comparação a abril de 2017 (série sem ajuste sazonal), o volume de serviços cresceu 2,2%, a taxa mais... http://agenciadenoticias.ibge.gov.br/agencia-sala-de-imprensa/2013-agencia-de-noticias/releases/21438-em-abril-setor-de-servicos-cresce-1-0-frente-a-marco.html 9229 9229|Pesquisa Mensal de Serviços|pesquisa-mensal-de-servicos|2076 9229 Release Em abril, setor de serviços cresce 1,0% frente a março 100 14/06/2018 09:00:00 true economicas 21451 {"image_intro":"","float_intro":"","image_intro_alt":"","image_intro_caption":"","image_fulltext":"images\/agenciadenoticias\